# 04/17/2023

In [15]:
import pandas as pd
df1 = pd.read_parquet("C:/Users/KeikoGolden/ComputationalLiguistics/KE235/sql_mongo_conflicts.parquet")
df1

serial_id    clashing_field  \
0     5be4ac1d383aea1b473330d6       skill_fr_fr   
1     5be4ac1d383aea1b473330d6       skill_es_es   
2     5be4ac1d383aea1b473330d6       skill_ja_jp   
3     5e55ad67870a2f223282b715       skill_en_us   
4     5ec5ddfebd86b3287e0fc75d  definition_en_us   
...                        ...               ...   
6660  62b22a87d1037db062c05987  definition_fr_fr   
6661  62b22a87d1037db062c05987  definition_fr_ca   
6662  62b22a87d1037db062c05987  definition_es_es   
6663  62b22a87d1037db062c05987  definition_ja_jp   
6664  62b22a87d1037db062c05987  definition_ko_kr   

                                              sql_value  \
0                                       Illustration 2D   
1                                        2d ilustración   
2                                                2Dイラスト   
3                                      A+ Certification   
4                                                  None   
...                                                 ...   
6660  Andon in Lean manufacturing est un système con...   
6661  Andon in Lean manufacturing est un système con...   
6662  Andon en Lean manufacturing es un sistema dise...   
6663  アンドオンは、リーン製造において経営者にリアルタイムで問題点を知らせ、直ちに是正措置が取れる...   
6664  안돈 시스템은 Lean 제조방식에 사용되며, 운영자와 관리자에게 실시간으로 문제를 ...   

                                            mongo_value  
0                                      Illustrations 2D  
1                                        Ilustración 2D  
2                                           2Dイラストレーション  
3                                      A+ certification  
4     Abrasive blasting, more commonly known as sand...  
...                                                 ...  
6660                                               None  
6661                                               None  
6662                                               None  
6663                                               None  
6664                                               None  

[6665 rows x 4 columns]

In [17]:
df1.to_excel('sql_mongo_conflicts.xlsx')

In [18]:
# Filter by skill_ja_jp and create a new df.
df2 = pd.DataFrame()
df2 = df1[df1.clashing_field == 'skill_ja_jp']
df2

serial_id clashing_field  \
2     5be4ac1d383aea1b473330d6    skill_ja_jp   
42    6182ba0b966b70a46b8c953e    skill_ja_jp   
50    5e01704215f9a609ddf2a589    skill_ja_jp   
66    5b11da33ed56ec1adea494e3    skill_ja_jp   
82    629226087d38ede8c191e7e7    skill_ja_jp   
...                        ...            ...   
6600  6113060ca9402ce7c12c5cd7    skill_ja_jp   
6612  5a9cf9d3fc0da84a0c1d9137    skill_ja_jp   
6624  5ef9e908c1a2cb03a7f33ba7    skill_ja_jp   
6635  5e41c4ebed09432018c02b0e    skill_ja_jp   
6647  5eac70da3bb20c3124504a48    skill_ja_jp   

                                       sql_value              mongo_value  
2                                         2Dイラスト              2Dイラストレーション  
42                                          None          AML/CTF規制知識（英国）  
50    A Mathematical Programming Language (AMPL)                     AMPL  
66                                          電話応答  電話応対 (Answering Phones)  
82                                          None            養殖コンテナのメンテナンス  
...                                          ...                      ...  
6600                                         行動派                  アクション志向  
6612                                       ガスボンベ                  シリンダー準備  
6624                                  学習コンテンツの開発             ラーニングコンテンツ開発  
6635                                        医療接遇                 患者との接触方法  
6647                                     現金自動支払機               TCR バランシング  

[557 rows x 4 columns]

In [19]:
# Secondly, we need to review, understand, and resolve the cases where the values between two databases are not identical.
df3 = pd.DataFrame()
df3 = df2[~df2.mongo_value.isnull()]
df3

serial_id clashing_field  \
2     5be4ac1d383aea1b473330d6    skill_ja_jp   
42    6182ba0b966b70a46b8c953e    skill_ja_jp   
50    5e01704215f9a609ddf2a589    skill_ja_jp   
66    5b11da33ed56ec1adea494e3    skill_ja_jp   
82    629226087d38ede8c191e7e7    skill_ja_jp   
...                        ...            ...   
6600  6113060ca9402ce7c12c5cd7    skill_ja_jp   
6612  5a9cf9d3fc0da84a0c1d9137    skill_ja_jp   
6624  5ef9e908c1a2cb03a7f33ba7    skill_ja_jp   
6635  5e41c4ebed09432018c02b0e    skill_ja_jp   
6647  5eac70da3bb20c3124504a48    skill_ja_jp   

                                       sql_value              mongo_value  
2                                         2Dイラスト              2Dイラストレーション  
42                                          None          AML/CTF規制知識（英国）  
50    A Mathematical Programming Language (AMPL)                     AMPL  
66                                          電話応答  電話応対 (Answering Phones)  
82                                          None            養殖コンテナのメンテナンス  
...                                          ...                      ...  
6600                                         行動派                  アクション志向  
6612                                       ガスボンベ                  シリンダー準備  
6624                                  学習コンテンツの開発             ラーニングコンテンツ開発  
6635                                        医療接遇                 患者との接触方法  
6647                                     現金自動支払機               TCR バランシング  

[555 rows x 4 columns]

# 04/18/2023

In [97]:
import sys
import importlib
sys.path.insert(0, ".")

import sql_functions as sf
from sql_functions import *
importlib.reload(sf)

<module 'sql_functions' from 'C:\\Users\\KeikoGolden\\ComputationalLiguistics\\Annotaion\\bn_nb_s\\PythonTocheckModel\\.\\sql_functions.py'>

In [98]:
import yaml
import psycopg2
from psycopg2.extensions import ISOLATION_LEVEL_AUTOCOMMIT
from psycopg2.extras import execute_values

with open("config.yml") as f:
    config = yaml.safe_load(f)

In [99]:
conn = psycopg2.connect(
        database=config['db']['name'], 
        user=config['db']['user'], 
        host=config['db']['host'], 
        password=config['db']['password']
    )

cur = conn.cursor()

In [100]:
import pandas as pd
df2 = pd.read_parquet("C:/Users/KeikoGolden/ComputationalLiguistics/KE235/sql_mongo_conflicts.parquet")
df2

serial_id    clashing_field  \
0     5be4ac1d383aea1b473330d6       skill_fr_fr   
1     5be4ac1d383aea1b473330d6       skill_es_es   
2     5be4ac1d383aea1b473330d6       skill_ja_jp   
3     5e55ad67870a2f223282b715       skill_en_us   
4     5ec5ddfebd86b3287e0fc75d  definition_en_us   
...                        ...               ...   
6660  62b22a87d1037db062c05987  definition_fr_fr   
6661  62b22a87d1037db062c05987  definition_fr_ca   
6662  62b22a87d1037db062c05987  definition_es_es   
6663  62b22a87d1037db062c05987  definition_ja_jp   
6664  62b22a87d1037db062c05987  definition_ko_kr   

                                              sql_value  \
0                                       Illustration 2D   
1                                        2d ilustración   
2                                                2Dイラスト   
3                                      A+ Certification   
4                                                  None   
...                                                 ...   
6660  Andon in Lean manufacturing est un système con...   
6661  Andon in Lean manufacturing est un système con...   
6662  Andon en Lean manufacturing es un sistema dise...   
6663  アンドオンは、リーン製造において経営者にリアルタイムで問題点を知らせ、直ちに是正措置が取れる...   
6664  안돈 시스템은 Lean 제조방식에 사용되며, 운영자와 관리자에게 실시간으로 문제를 ...   

                                            mongo_value  
0                                      Illustrations 2D  
1                                        Ilustración 2D  
2                                           2Dイラストレーション  
3                                      A+ certification  
4     Abrasive blasting, more commonly known as sand...  
...                                                 ...  
6660                                               None  
6661                                               None  
6662                                               None  
6663                                               None  
6664                                               None  

[6665 rows x 4 columns]

In [101]:
df2['serial_id'].value_counts()

5e02c32a15f9a609ddf63370    14
5ec5e258ec223f743f88568d    13
5e6189eae71c53599180e350    13
5c352b672349e96712c006e4    13
5adcfa7fdccd3b50f3737a16    13
                            ..
5c352c76eebc546524b710c0     1
629226017d38ede8c191e71f     1
5f20264d537d4436df7df72f     1
5a99c356fc0da84a0c16c2cd     1
5e02b77b15f9a609ddf6024b     1
Name: serial_id, Length: 1373, dtype: int64

In [102]:
df3 = df2.drop_duplicates(subset=['serial_id']).reset_index(drop=True)
df3

serial_id    clashing_field  \
0     5be4ac1d383aea1b473330d6       skill_fr_fr   
1     5e55ad67870a2f223282b715       skill_en_us   
2     5ec5ddfebd86b3287e0fc75d  definition_en_us   
3     5a99c60dfc0da84a0c16c792       skill_ko_kr   
4     5c2c3d12bb4cfc70c300b0e3  definition_fr_fr   
...                        ...               ...   
1368  5a9cf9d3fc0da84a0c1d9137       skill_fr_fr   
1369  5ef9e908c1a2cb03a7f33ba7       skill_fr_fr   
1370  5e41c4ebed09432018c02b0e       skill_fr_fr   
1371  5eac70da3bb20c3124504a48       skill_fr_fr   
1372  62b22a87d1037db062c05987       skill_fr_fr   

                                     sql_value  \
0                              Illustration 2D   
1                             A+ Certification   
2                                         None   
3                                           투약   
4                                         None   
...                                        ...   
1368                          Bouteille de Gaz   
1369  Développement de Contenu d'Apprentissage   
1370                   Engagement des Patients   
1371                  dispensateur de Caissier   
1372                                     Andon   

                                            mongo_value  
0                                      Illustrations 2D  
1                                      A+ certification  
2     Abrasive blasting, more commonly known as sand...  
3                           투약 (Administering Medicine)  
4     Adobe Creative Cloud est un ensemble d'applica...  
...                                                 ...  
1368                          Préparation des cylindres  
1369           Développement de contenu d'apprentissage  
1370              Techniques de contact avec le patient  
1371                                 Équilibrage du TCR  
1372                                               None  

[1373 rows x 4 columns]

In [103]:
df3['serial_id'].to_excel('common_serial_id_across_lang.xlsx')

In [104]:
#  serial_idを使ってdb_idを得る関数。オプション１。
def get_db_id(serial_id):
    command = """
    select id from skills where serial_id = %s
    """
    df4 = pd.read_sql(command, conn, params=(serial_id,))
    return df4

In [69]:
#  serial_idを使ってdb_idを得る関数。オプション２。
def get_db_id(serial_id):
    command = """
    select * from skills where serial_id = %(serial_id)s
    """
    df4 = pd.read_sql(command, conn, params={"serial_id": serial_id})
    
    return df4

In [75]:
#  serial_idを使ってdb_idを得る関数
#
#def get_db_id(serial_id):
#    
#    command = """
#    select * from skills where serial_id=%s
#    """
#    df4 = pd.read_sql(command, conn, serial_id)
#    
#    return df4

In [105]:
#  serial_idを使ってdb_idを得る関数を呼ぶ。

df5 = pd.DataFrame()
for serial_num in df3.serial_id:
    df6 = get_db_id(serial_num)
    df5 = df5.append(df6)

C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\1528119694.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\1528119694.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.


C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\1528119694.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\1528119694.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLA

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\1528119694.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\1528119694.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLA

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\1528119694.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\1528119694.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLA

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\1528119694.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\1528119694.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLA

...

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\1528119694.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\1528119694.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLA

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\1528119694.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\1528119694.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLA

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\1528119694.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\1528119694.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLA

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\1528119694.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\1528119694.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLA

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\1528119694.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\1528119694.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLA

In [81]:
df5

id
0      11
0      38
0      54
0     163
0     182
..    ...
0   12474
0   12475
0   12477
0   12478
0   12715

[1373 rows x 1 columns]

In [107]:
# df5のdb_idを使ってすべてのLocaleを合わせたテーブルを作成する関数。
def show_missing_values_across_locale(db_id1, db_id2, db_id3, db_id4, db_id5, db_id6, db_id7, db_id8, db_id9, db_id10):

    command = """
    select skills.skill, skills_en_gb.skill as gb, skills_en_us.skill as en, skills_de_de.skill as de,skills_es_es.skill as es, skills_fr_ca.skill as fr_ca,skills_fr_fr.skill as fr, skills_it_it.skill as it,skills_ja_jp.skill as jp,skills_ko_kr.skill as ko from skills, skills_en_gb, skills_en_us, skills_de_de,skills_es_es, skills_fr_ca,skills_fr_fr, skills_it_it, skills_ja_jp,skills_ko_kr
    where skills.id = %s and skills_en_gb.skill_id = %s and skills_en_us.skill_id = %s and skills_de_de.skill_id = %s and skills_es_es.skill_id = %s and skills_fr_ca.skill_id = %s and skills_fr_fr.skill_id = %s and skills_it_it.skill_id = %s and skills_ja_jp.skill_id = %s and skills_ko_kr.skill_id = %s
    """
    df4 = pd.read_sql(command, conn, params=(db_id1, db_id2, db_id3, db_id4, db_id5, db_id6, db_id7, db_id8, db_id9, db_id10,))
    return df4   

In [108]:
# df5のdb_idを使ってすべてのLocaleを合わせたテーブルを作成する関数を呼ぶ。

df7 = pd.DataFrame()
for db_num in df5.id:
    df8 = show_missing_values_across_locale(db_num, db_num, db_num, db_num, db_num, db_num, db_num, db_num, db_num, db_num)
    df7 = df7.append(df8)

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\150627410.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\150627410.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlc

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\150627410.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\150627410.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlc

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\150627410.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\150627410.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlc

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\150627410.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\150627410.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlc

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\150627410.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\150627410.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlc

...

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\150627410.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\150627410.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlc

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\150627410.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\150627410.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlc

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\150627410.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\150627410.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlc

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\150627410.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\150627410.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlc

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\150627410.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\150627410.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlc

In [109]:
df7

skill                            gb  \
0                2D Illustration               2D Illustration   
0               A+ Certification              A+ Certification   
0              Abrasive Blasting             Abrasive Blasting   
0         Administering Medicine        Administering Medicine   
0           Adobe Creative Cloud          Adobe Creative Cloud   
..                           ...                           ...   
0                   Gas Cylinder                  Gas Cylinder   
0   Learning Content Development  Learning Content Development   
0             Patient Engagement            Patient Engagement   
0          Teller Cash Dispenser         Teller Cash Dispenser   
0                          Andon                         Andon   

                              en                                  de  \
0                2D Illustration                        2D-Abbildung   
0               A+ Certification                   A+ Zertifizierung   
0              Abrasive Blasting                  Abrasives Strahlen   
0         Administering Medicine      Verabreichung von Medikamenten   
0           Adobe Creative Cloud                Adobe Creative Cloud   
..                           ...                                 ...   
0                   Gas Cylinder                Zylinderpräparierung   
0   Learning Content Development        Entwicklung von Lerninhalten   
0             Patient Engagement  Techniken für den Patientenkontakt   
0          Teller Cash Dispenser                       TCR-Ausgleich   
0                          Andon                               Andon   

                                        es  \
0                           2d ilustración   
0                         Certificación A+   
0                      Granallado abrasivo   
0           Administración de medicamentos   
0                     Adobe Creative Cloud   
..                                     ...   
0                          Cilindro de Gas   
0   desarrollo de Contenido de Aprendizaje   
0                  Compromiso del Paciente   
0        dispensador de Efectivo de Cajero   
0                                    Andon   

                                       fr_ca  \
0                            Illustration 2D   
0                           Certification A+   
0                         Nettoyage abrasive   
0                Administrer des médicaments   
0                       Adobe Creative Cloud   
..                                       ...   
0                           Bouteille de Gaz   
0   Développement de Contenu d'Apprentissage   
0                    Engagement des Patients   
0                   dispensateur de Caissier   
0                                      Andon   

                                          fr  \
0                            Illustration 2D   
0                           Certification A+   
0                           Décapage abrasif   
0                Administrer des médicaments   
0                       Adobe Creative Cloud   
..                                       ...   
0                           Bouteille de Gaz   
0   Développement de Contenu d'Apprentissage   
0                    Engagement des Patients   
0                   dispensateur de Caissier   
0                                      Andon   

                                            it                    jp  \
0                             Illustrazione 2D                2Dイラスト   
0                            Certificazione A+                A+認定資格   
0              Sabbiatrice (Abrasive Blasting)                 吹付け加工   
0                       Somministrare medicine                  薬剤投与   
0                         Adobe Creative Cloud  Adobe Creative Cloud   
..                                         ...                   ...   
0                             Cilindro del Gas                 ガスボンベ   
0   Apprendimento dello Sviluppo dei Contenuti            学習コンテンツの開発   
0             

In [111]:
df7["serial_id"] = df3['serial_id']
df7

skill                            gb  \
0                2D Illustration               2D Illustration   
0               A+ Certification              A+ Certification   
0              Abrasive Blasting             Abrasive Blasting   
0         Administering Medicine        Administering Medicine   
0           Adobe Creative Cloud          Adobe Creative Cloud   
..                           ...                           ...   
0                   Gas Cylinder                  Gas Cylinder   
0   Learning Content Development  Learning Content Development   
0             Patient Engagement            Patient Engagement   
0          Teller Cash Dispenser         Teller Cash Dispenser   
0                          Andon                         Andon   

                              en                                  de  \
0                2D Illustration                        2D-Abbildung   
0               A+ Certification                   A+ Zertifizierung   
0              Abrasive Blasting                  Abrasives Strahlen   
0         Administering Medicine      Verabreichung von Medikamenten   
0           Adobe Creative Cloud                Adobe Creative Cloud   
..                           ...                                 ...   
0                   Gas Cylinder                Zylinderpräparierung   
0   Learning Content Development        Entwicklung von Lerninhalten   
0             Patient Engagement  Techniken für den Patientenkontakt   
0          Teller Cash Dispenser                       TCR-Ausgleich   
0                          Andon                               Andon   

                                        es  \
0                           2d ilustración   
0                         Certificación A+   
0                      Granallado abrasivo   
0           Administración de medicamentos   
0                     Adobe Creative Cloud   
..                                     ...   
0                          Cilindro de Gas   
0   desarrollo de Contenido de Aprendizaje   
0                  Compromiso del Paciente   
0        dispensador de Efectivo de Cajero   
0                                    Andon   

                                       fr_ca  \
0                            Illustration 2D   
0                           Certification A+   
0                         Nettoyage abrasive   
0                Administrer des médicaments   
0                       Adobe Creative Cloud   
..                                       ...   
0                           Bouteille de Gaz   
0   Développement de Contenu d'Apprentissage   
0                    Engagement des Patients   
0                   dispensateur de Caissier   
0                                      Andon   

                                          fr  \
0                            Illustration 2D   
0                           Certification A+   
0                           Décapage abrasif   
0                Administrer des médicaments   
0                       Adobe Creative Cloud   
..                                       ...   
0                           Bouteille de Gaz   
0   Développement de Contenu d'Apprentissage   
0                    Engagement des Patients   
0                   dispensateur de Caissier   
0                                      Andon   

                                            it                    jp  \
0                             Illustrazione 2D                2Dイラスト   
0                            Certificazione A+                A+認定資格   
0              Sabbiatrice (Abrasive Blasting)                 吹付け加工   
0                       Somministrare medicine                  薬剤投与   
0                         Adobe Creative Cloud  Adobe Creative Cloud   
..                                         ...                   ...   
0                             Cilindro del Gas                 ガスボンベ   
0   Apprendimento dello Sviluppo dei Contenuti            学習コンテンツの開発   
0             

In [112]:
df7.to_excel('common_gap_across_lang.xlsx')

# 04/18/2023 - without German

In [189]:
import sys
import importlib
sys.path.insert(0, ".")

import sql_functions as sf
from sql_functions import *
importlib.reload(sf)

<module 'sql_functions' from 'C:\\Users\\KeikoGolden\\ComputationalLiguistics\\Annotaion\\bn_nb_s\\PythonTocheckModel\\.\\sql_functions.py'>

In [190]:
import yaml
import psycopg2
from psycopg2.extensions import ISOLATION_LEVEL_AUTOCOMMIT
from psycopg2.extras import execute_values

with open("config.yml") as f:
    config = yaml.safe_load(f)

In [191]:
conn = psycopg2.connect(
        database=config['db']['name'], 
        user=config['db']['user'], 
        host=config['db']['host'], 
        password=config['db']['password']
    )

cur = conn.cursor()

In [232]:
import pandas as pd
df2 = pd.read_excel("C:/Users/KeikoGolden/ComputationalLiguistics/Annotaion/bn_nb_s/PythonTocheckModel/sql_mongo_conflicts.xlsx")
df2

Unnamed: 0                 serial_id    clashing_field  \
0              0  5be4ac1d383aea1b473330d6       skill_fr_fr   
1              1  5be4ac1d383aea1b473330d6       skill_es_es   
2              2  5be4ac1d383aea1b473330d6       skill_ja_jp   
3              3  5e55ad67870a2f223282b715       skill_en_us   
4              4  5ec5ddfebd86b3287e0fc75d  definition_en_us   
...          ...                       ...               ...   
6572        6660  62b22a87d1037db062c05987  definition_fr_fr   
6573        6661  62b22a87d1037db062c05987  definition_fr_ca   
6574        6662  62b22a87d1037db062c05987  definition_es_es   
6575        6663  62b22a87d1037db062c05987  definition_ja_jp   
6576        6664  62b22a87d1037db062c05987  definition_ko_kr   

                                              sql_value  \
0                                       Illustration 2D   
1                                        2d ilustración   
2                                                2Dイラスト   
3                                      A+ Certification   
4                                                   NaN   
...                                                 ...   
6572  Andon in Lean manufacturing est un système con...   
6573  Andon in Lean manufacturing est un système con...   
6574  Andon en Lean manufacturing es un sistema dise...   
6575  アンドオンは、リーン製造において経営者にリアルタイムで問題点を知らせ、直ちに是正措置が取れる...   
6576  안돈 시스템은 Lean 제조방식에 사용되며, 운영자와 관리자에게 실시간으로 문제를 ...   

                                            mongo_value  
0                                      Illustrations 2D  
1                                        Ilustración 2D  
2                                           2Dイラストレーション  
3                                      A+ certification  
4     Abrasive blasting, more commonly known as sand...  
...                                                 ...  
6572                                                NaN  
6573                                                NaN  
6574                                                NaN  
6575                                                NaN  
6576                                                NaN  

[6577 rows x 5 columns]

In [233]:
df3 = df2.drop_duplicates(subset=['serial_id']).reset_index(drop=True)
df3

Unnamed: 0                 serial_id    clashing_field  \
0              0  5be4ac1d383aea1b473330d6       skill_fr_fr   
3              3  5e55ad67870a2f223282b715       skill_en_us   
4              4  5ec5ddfebd86b3287e0fc75d  definition_en_us   
10            10  5a99c60dfc0da84a0c16c792       skill_ko_kr   
16            16  5c2c3d12bb4cfc70c300b0e3  definition_fr_fr   
...          ...                       ...               ...   
6520        6608  5a9cf9d3fc0da84a0c1d9137       skill_fr_fr   
6532        6620  5ef9e908c1a2cb03a7f33ba7       skill_fr_fr   
6543        6631  5e41c4ebed09432018c02b0e       skill_fr_fr   
6555        6643  5eac70da3bb20c3124504a48       skill_fr_fr   
6567        6655  62b22a87d1037db062c05987       skill_fr_fr   

                                     sql_value  \
0                              Illustration 2D   
3                             A+ Certification   
4                                          NaN   
10                                          투약   
16                                         NaN   
...                                        ...   
6520                          Bouteille de Gaz   
6532  Développement de Contenu d'Apprentissage   
6543                   Engagement des Patients   
6555                  dispensateur de Caissier   
6567                                     Andon   

                                            mongo_value  
0                                      Illustrations 2D  
3                                      A+ certification  
4     Abrasive blasting, more commonly known as sand...  
10                          투약 (Administering Medicine)  
16    Adobe Creative Cloud est un ensemble d'applica...  
...                                                 ...  
6520                          Préparation des cylindres  
6532           Développement de contenu d'apprentissage  
6543              Techniques de contact avec le patient  
6555                                 Équilibrage du TCR  
6567                                                NaN  

[1370 rows x 5 columns]

In [234]:
#df3 = df2.drop_duplicates(subset=['serial_id']).reset_index(drop=True)
#df3

In [235]:
def get_db_id(serial_id):
    command = """
    select id from skills where serial_id = %s
    """
    df4 = pd.read_sql(command, conn, params=(serial_id,))
    return df4

In [236]:
#  serial_idを使ってdb_idを得る関数を呼ぶ。

df5 = pd.DataFrame()
for serial_num in df3.serial_id:
    df6 = get_db_id(serial_num)
    df5 = df5.append(df6)

C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\1528119694.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\1528119694.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.


C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\1528119694.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\1528119694.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLA

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\1528119694.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\1528119694.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLA

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\1528119694.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\1528119694.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLA

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\1528119694.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\1528119694.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLA

...

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\1528119694.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\1528119694.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLA

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\1528119694.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\1528119694.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLA

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\1528119694.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\1528119694.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLA

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\1528119694.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\1528119694.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLA

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\1528119694.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)


In [237]:
df5 = df.5reset_index(drop=True)
df5

id
0      11
0      38
0      54
0     163
0     182
..    ...
0   12474
0   12475
0   12477
0   12478
0   12715

[1370 rows x 1 columns]

In [245]:
def show_missing_values_across_locale(db_id1, db_id2, db_id3, db_id4, db_id5, db_id6, db_id7, db_id8, db_id9):

    command = """
    select skills.skill, skills_en_gb.skill as gb, skills_en_us.skill as en, skills_es_es.skill as es, skills_fr_ca.skill as fr_ca, skills_fr_fr.skill as fr, skills_it_it.skill as it, skills_ja_jp.skill as jp, skills_ko_kr.skill as ko, skills_en_gb.skill_definition as gb_def, skills_en_us.skill_definition as us_def, skills_es_es.skill_definition as es_def, skills_fr_ca.skill_definition as fr_ca_def, skills_fr_fr.skill_definition as fr_def, skills_ja_jp.skill_definition as ja_def, skills_ko_kr.skill_definition as ko_def from skills, skills_en_gb, skills_en_us, skills_es_es, skills_fr_ca, skills_fr_fr, skills_it_it, skills_ja_jp, skills_ko_kr
    where skills.id = %s and skills_en_gb.skill_id = %s and skills_en_us.skill_id = %s and skills_es_es.skill_id = %s and skills_fr_ca.skill_id = %s and skills_fr_fr.skill_id = %s and skills_it_it.skill_id = %s and skills_ja_jp.skill_id = %s and skills_ko_kr.skill_id = %s
    """
    df4 = pd.read_sql(command, conn, params=(db_id1, db_id2, db_id3, db_id4, db_id5, db_id6, db_id7, db_id8, db_id9,))
    return df4 

In [246]:
# df5のdb_idを使ってすべてのLocaleを合わせたテーブルを作成する関数を呼ぶ。

df7 = pd.DataFrame()
for db_num in df5.id:
    df8 = show_missing_values_across_locale(db_num, db_num, db_num, db_num, db_num, db_num, db_num, db_num, db_num)
    df7 = df7.append(df8)

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\3421641193.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\3421641193.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLA

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\3421641193.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\3421641193.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLA

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\3421641193.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\3421641193.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLA

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\3421641193.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\3421641193.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLA

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\3421641193.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\3421641193.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLA

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\3421641193.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\3421641193.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLA

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\3421641193.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\3421641193.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLA

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\3421641193.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\3421641193.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLA

KeyboardInterrupt: 

In [243]:
df7

skill                            gb  \
0                2D Illustration               2D Illustration   
0               A+ Certification              A+ Certification   
0              Abrasive Blasting             Abrasive Blasting   
0         Administering Medicine        Administering Medicine   
0           Adobe Creative Cloud          Adobe Creative Cloud   
..                           ...                           ...   
0                   Gas Cylinder                  Gas Cylinder   
0   Learning Content Development  Learning Content Development   
0             Patient Engagement            Patient Engagement   
0          Teller Cash Dispenser         Teller Cash Dispenser   
0                          Andon                         Andon   

                              en                                      es  \
0                2D Illustration                          2d ilustración   
0               A+ Certification                        Certificación A+   
0              Abrasive Blasting                     Granallado abrasivo   
0         Administering Medicine          Administración de medicamentos   
0           Adobe Creative Cloud                    Adobe Creative Cloud   
..                           ...                                     ...   
0                   Gas Cylinder                         Cilindro de Gas   
0   Learning Content Development  desarrollo de Contenido de Aprendizaje   
0             Patient Engagement                 Compromiso del Paciente   
0          Teller Cash Dispenser       dispensador de Efectivo de Cajero   
0                          Andon                                   Andon   

                                       fr_ca  \
0                            Illustration 2D   
0                           Certification A+   
0                         Nettoyage abrasive   
0                Administrer des médicaments   
0                       Adobe Creative Cloud   
..                                       ...   
0                           Bouteille de Gaz   
0   Développement de Contenu d'Apprentissage   
0                    Engagement des Patients   
0                   dispensateur de Caissier   
0                                      Andon   

                                          fr  \
0                            Illustration 2D   
0                           Certification A+   
0                           Décapage abrasif   
0                Administrer des médicaments   
0                       Adobe Creative Cloud   
..                                       ...   
0                           Bouteille de Gaz   
0   Développement de Contenu d'Apprentissage   
0                    Engagement des Patients   
0                   dispensateur de Caissier   
0                                      Andon   

                                            it                    jp  \
0                             Illustrazione 2D                2Dイラスト   
0                            Certificazione A+                A+認定資格   
0              Sabbiatrice (Abrasive Blasting)                 吹付け加工   
0                       Somministrare medicine                  薬剤投与   
0                         Adobe Creative Cloud  Adobe Creative Cloud   
..                                         ...                   ...   
0                             Cilindro del Gas                 ガスボンベ   
0   Apprendimento dello Sviluppo dei Contenuti            学習コンテンツの開発   
0                         Impegno del Paziente                  医療接遇   
0               distributore di Cassa di Cassa               現金自動支払機   
0                                        Andon                  アンドン   

                      ko                                             gb_def  \
0                2D 일러스트  An illustration is a decoration, interpretatio...   
0                A+ 자격인증  A+ (A Plus) is an entry-level computer certifi...   
0                  연마 가공                                         

In [241]:
#df7['serial_id'] = df3['serial_id']

In [242]:
df7 = df7.reset_index(drop=True)
df7

skill                            gb  \
0                2D Illustration               2D Illustration   
0               A+ Certification              A+ Certification   
0              Abrasive Blasting             Abrasive Blasting   
0         Administering Medicine        Administering Medicine   
0           Adobe Creative Cloud          Adobe Creative Cloud   
..                           ...                           ...   
0                   Gas Cylinder                  Gas Cylinder   
0   Learning Content Development  Learning Content Development   
0             Patient Engagement            Patient Engagement   
0          Teller Cash Dispenser         Teller Cash Dispenser   
0                          Andon                         Andon   

                              en                                      es  \
0                2D Illustration                          2d ilustración   
0               A+ Certification                        Certificación A+   
0              Abrasive Blasting                     Granallado abrasivo   
0         Administering Medicine          Administración de medicamentos   
0           Adobe Creative Cloud                    Adobe Creative Cloud   
..                           ...                                     ...   
0                   Gas Cylinder                         Cilindro de Gas   
0   Learning Content Development  desarrollo de Contenido de Aprendizaje   
0             Patient Engagement                 Compromiso del Paciente   
0          Teller Cash Dispenser       dispensador de Efectivo de Cajero   
0                          Andon                                   Andon   

                                       fr_ca  \
0                            Illustration 2D   
0                           Certification A+   
0                         Nettoyage abrasive   
0                Administrer des médicaments   
0                       Adobe Creative Cloud   
..                                       ...   
0                           Bouteille de Gaz   
0   Développement de Contenu d'Apprentissage   
0                    Engagement des Patients   
0                   dispensateur de Caissier   
0                                      Andon   

                                          fr  \
0                            Illustration 2D   
0                           Certification A+   
0                           Décapage abrasif   
0                Administrer des médicaments   
0                       Adobe Creative Cloud   
..                                       ...   
0                           Bouteille de Gaz   
0   Développement de Contenu d'Apprentissage   
0                    Engagement des Patients   
0                   dispensateur de Caissier   
0                                      Andon   

                                            it                    jp  \
0                             Illustrazione 2D                2Dイラスト   
0                            Certificazione A+                A+認定資格   
0              Sabbiatrice (Abrasive Blasting)                 吹付け加工   
0                       Somministrare medicine                  薬剤投与   
0                         Adobe Creative Cloud  Adobe Creative Cloud   
..                                         ...                   ...   
0                             Cilindro del Gas                 ガスボンベ   
0   Apprendimento dello Sviluppo dei Contenuti            学習コンテンツの開発   
0                         Impegno del Paziente                  医療接遇   
0               distributore di Cassa di Cassa               現金自動支払機   
0                                        Andon                  アンドン   

                      ko                                             gb_def  \
0                2D 일러스트  An illustration is a decoration, interpretatio...   
0                A+ 자격인증  A+ (A Plus) is an entry-level computer certifi...   
0                  연마 가공                                         

In [225]:
#インデックス番号がdf３とdf７とでマッチしないので、マージは使えない。
df9 = pd.merge(df3[['serial_id']], df7, left_index = True, right_index = True )

In [218]:
#この場合はConcatを使う
#df9 = pd.concat([df3.serial_id, df7])

In [226]:
df9

serial_id                         skill  \
0   5be4ac1d383aea1b473330d6               2D Illustration   
0   5be4ac1d383aea1b473330d6              A+ Certification   
0   5be4ac1d383aea1b473330d6             Abrasive Blasting   
0   5be4ac1d383aea1b473330d6        Administering Medicine   
0   5be4ac1d383aea1b473330d6          Adobe Creative Cloud   
..                       ...                           ...   
0   5be4ac1d383aea1b473330d6                  Gas Cylinder   
0   5be4ac1d383aea1b473330d6  Learning Content Development   
0   5be4ac1d383aea1b473330d6            Patient Engagement   
0   5be4ac1d383aea1b473330d6         Teller Cash Dispenser   
0   5be4ac1d383aea1b473330d6                         Andon   

                              gb                            en  \
0                2D Illustration               2D Illustration   
0               A+ Certification              A+ Certification   
0              Abrasive Blasting             Abrasive Blasting   
0         Administering Medicine        Administering Medicine   
0           Adobe Creative Cloud          Adobe Creative Cloud   
..                           ...                           ...   
0                   Gas Cylinder                  Gas Cylinder   
0   Learning Content Development  Learning Content Development   
0             Patient Engagement            Patient Engagement   
0          Teller Cash Dispenser         Teller Cash Dispenser   
0                          Andon                         Andon   

                                        es  \
0                           2d ilustración   
0                         Certificación A+   
0                      Granallado abrasivo   
0           Administración de medicamentos   
0                     Adobe Creative Cloud   
..                                     ...   
0                          Cilindro de Gas   
0   desarrollo de Contenido de Aprendizaje   
0                  Compromiso del Paciente   
0        dispensador de Efectivo de Cajero   
0                                    Andon   

                                       fr_ca  \
0                            Illustration 2D   
0                           Certification A+   
0                         Nettoyage abrasive   
0                Administrer des médicaments   
0                       Adobe Creative Cloud   
..                                       ...   
0                           Bouteille de Gaz   
0   Développement de Contenu d'Apprentissage   
0                    Engagement des Patients   
0                   dispensateur de Caissier   
0                                      Andon   

                                          fr  \
0                            Illustration 2D   
0                           Certification A+   
0                           Décapage abrasif   
0                Administrer des médicaments   
0                       Adobe Creative Cloud   
..                                       ...   
0                           Bouteille de Gaz   
0   Développement de Contenu d'Apprentissage   
0                    Engagement des Patients   
0                   dispensateur de Caissier   
0                                      Andon   

                                            it                    jp  \
0                             Illustrazione 2D                2Dイラスト   
0                            Certificazione A+                A+認定資格   
0              Sabbiatrice (Abrasive Blasting)                 吹付け加工   
0                       Somministrare medicine                  薬剤投与   
0                         Adobe Creative Cloud  Adobe Creative Cloud   
..                                         ...                   ...   
0                             Cilindro del Gas                 ガスボンベ   
0   Apprendimento dello Sviluppo dei Contenuti            学習コンテンツの開発   
0                         Impegno del Paziente                  医療接遇   
0               distributore di Cassa di Cassa        

In [220]:
df9.to_excel('common_gap_across_lang_without_german.xlsx')

# 04/19/2023 - match all the data in parquet to SQL data

In [313]:
import sys
import importlib
sys.path.insert(0, ".")

import sql_functions as sf
from sql_functions import *
importlib.reload(sf)

<module 'sql_functions' from 'C:\\Users\\KeikoGolden\\ComputationalLiguistics\\Annotaion\\bn_nb_s\\PythonTocheckModel\\.\\sql_functions.py'>

In [314]:
import yaml
import psycopg2
from psycopg2.extensions import ISOLATION_LEVEL_AUTOCOMMIT
from psycopg2.extras import execute_values

with open("config.yml") as f:
    config = yaml.safe_load(f)

In [315]:
conn = psycopg2.connect(
        database=config['db']['name'], 
        user=config['db']['user'], 
        host=config['db']['host'], 
        password=config['db']['password']
    )

cur = conn.cursor()

In [362]:
import pandas as pd
import pandas as pd
df2 = pd.read_parquet("C:/Users/KeikoGolden/ComputationalLiguistics/KE235/sql_mongo_conflicts2.parquet")
df2

serial_id    clashing_field  \
0     5be4ac1d383aea1b473330d6       skill_fr_fr   
1     5be4ac1d383aea1b473330d6       skill_es_es   
2     5be4ac1d383aea1b473330d6       skill_ja_jp   
3     5e55ad67870a2f223282b715       skill_en_us   
4     5ec5ddfebd86b3287e0fc75d  definition_en_us   
...                        ...               ...   
6660  62b22a87d1037db062c05987  definition_fr_fr   
6661  62b22a87d1037db062c05987  definition_fr_ca   
6662  62b22a87d1037db062c05987  definition_es_es   
6663  62b22a87d1037db062c05987  definition_ja_jp   
6664  62b22a87d1037db062c05987  definition_ko_kr   

                                              sql_value  \
0                                       Illustration 2D   
1                                        2d ilustración   
2                                                2Dイラスト   
3                                      A+ Certification   
4                                                  None   
...                                                 ...   
6660  Andon in Lean manufacturing est un système con...   
6661  Andon in Lean manufacturing est un système con...   
6662  Andon en Lean manufacturing es un sistema dise...   
6663  アンドオンは、リーン製造において経営者にリアルタイムで問題点を知らせ、直ちに是正措置が取れる...   
6664  안돈 시스템은 Lean 제조방식에 사용되며, 운영자와 관리자에게 실시간으로 문제를 ...   

                                            mongo_value  \
0                                      Illustrations 2D   
1                                        Ilustración 2D   
2                                           2Dイラストレーション   
3                                      A+ certification   
4     Abrasive blasting, more commonly known as sand...   
...                                                 ...   
6660                                               None   
6661                                               None   
6662                                               None   
6663                                               None   
6664                                               None   

                                               resolved  
0                                       Illustration 2D  
1                                        2d ilustración  
2                                                2Dイラスト  
3                                      A+ Certification  
4     Abrasive blasting, more commonly known as sand...  
...                                                 ...  
6660  Andon in Lean manufacturing est un système con...  
6661  Andon in Lean manufacturing est un système con...  
6662  Andon en Lean manufacturing es un sistema dise...  
6663  アンドオンは、リーン製造において経営者にリアルタイムで問題点を知らせ、直ちに是正措置が取れる...  
6664  안돈 시스템은 Lean 제조방식에 사용되며, 운영자와 관리자에게 실시간으로 문제를 ...  

[6665 rows x 5 columns]

In [363]:
df2 = df2.drop_duplicates(subset=['serial_id']).reset_index(drop=True)
df2

serial_id    clashing_field  \
0     5be4ac1d383aea1b473330d6       skill_fr_fr   
1     5e55ad67870a2f223282b715       skill_en_us   
2     5ec5ddfebd86b3287e0fc75d  definition_en_us   
3     5a99c60dfc0da84a0c16c792       skill_ko_kr   
4     5c2c3d12bb4cfc70c300b0e3  definition_fr_fr   
...                        ...               ...   
1368  5a9cf9d3fc0da84a0c1d9137       skill_fr_fr   
1369  5ef9e908c1a2cb03a7f33ba7       skill_fr_fr   
1370  5e41c4ebed09432018c02b0e       skill_fr_fr   
1371  5eac70da3bb20c3124504a48       skill_fr_fr   
1372  62b22a87d1037db062c05987       skill_fr_fr   

                                     sql_value  \
0                              Illustration 2D   
1                             A+ Certification   
2                                         None   
3                                           투약   
4                                         None   
...                                        ...   
1368                          Bouteille de Gaz   
1369  Développement de Contenu d'Apprentissage   
1370                   Engagement des Patients   
1371                  dispensateur de Caissier   
1372                                     Andon   

                                            mongo_value  \
0                                      Illustrations 2D   
1                                      A+ certification   
2     Abrasive blasting, more commonly known as sand...   
3                           투약 (Administering Medicine)   
4     Adobe Creative Cloud est un ensemble d'applica...   
...                                                 ...   
1368                          Préparation des cylindres   
1369           Développement de contenu d'apprentissage   
1370              Techniques de contact avec le patient   
1371                                 Équilibrage du TCR   
1372                                               None   

                                               resolved  
0                                       Illustration 2D  
1                                      A+ Certification  
2     Abrasive blasting, more commonly known as sand...  
3                                                    투약  
4     Adobe Creative Cloud est un ensemble d'applica...  
...                                                 ...  
1368                                   Bouteille de Gaz  
1369           Développement de Contenu d'Apprentissage  
1370                            Engagement des Patients  
1371                           dispensateur de Caissier  
1372                                              Andon  

[1373 rows x 5 columns]

In [364]:
def get_db_id(serial_id):
    command = """
    select id from skills where serial_id = %s
    """
    df4 = pd.read_sql(command, conn, params=(serial_id,))
    return df4

In [365]:
#  serial_idを使ってdb_idを得る関数を呼ぶ。

df5 = pd.DataFrame()
for serial_num in df2.serial_id:
    df6 = get_db_id(serial_num)
    df5 = df5.append(df6)

C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\573298178.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\573298178.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\573298178.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\573298178.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlc

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\573298178.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\573298178.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlc

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\573298178.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\573298178.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlc

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\573298178.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\573298178.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlc

...

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\573298178.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\573298178.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlc

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\573298178.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\573298178.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlc

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\573298178.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\573298178.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlc

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\573298178.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\573298178.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlc

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\573298178.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\573298178.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df5 = df5.append(df6)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlc

In [366]:
df5 = df5.reset_index(drop=True)
df5

id
0        11
1        38
2        54
3       163
4       182
...     ...
1368  12474
1369  12475
1370  12477
1371  12478
1372  12715

[1373 rows x 1 columns]

In [367]:
def show_missing_values_across_locale(db_id1, db_id2, db_id3, db_id4, db_id5, db_id6, db_id7, db_id8, db_id9, db_id10):

    command = """
    select skills.skill, skills_en_gb.skill as gb, skills_en_us.skill as en, skills_de_de.skill as de, skills_es_es.skill as es, skills_fr_ca.skill as fr_ca, skills_fr_fr.skill as fr, skills_it_it.skill as it, skills_ja_jp.skill as jp, skills_ko_kr.skill as ko, skills_en_gb.skill_definition as gb_def, skills_en_us.skill_definition as us_def, skills_de_de.skill_definition, skills_es_es.skill_definition as es_def, skills_fr_ca.skill_definition as fr_ca_def, skills_fr_fr.skill_definition as fr_def, skills_it_it.skill_definition, skills_ja_jp.skill_definition as ja_def, skills_ko_kr.skill_definition as ko_def from skills, skills_en_gb, skills_en_us, skills_de_de, skills_es_es, skills_fr_ca, skills_fr_fr, skills_it_it, skills_ja_jp, skills_ko_kr
    where skills.id = %s and skills_en_gb.skill_id = %s and skills_en_us.skill_id = %s and skills_de_de.skill_id = %s and skills_es_es.skill_id = %s and skills_fr_ca.skill_id = %s and skills_fr_fr.skill_id = %s and skills_it_it.skill_id = %s and skills_ja_jp.skill_id = %s and skills_ko_kr.skill_id = %s
    """
    df4 = pd.read_sql(command, conn, params=(db_id1, db_id2, db_id3, db_id4, db_id5, db_id6, db_id7, db_id8, db_id9, db_id10,))
    return df4 

In [348]:
#Option 1 - でもこれはデータフレームになるとカラムがなくなってしまう。
####!!!!　appendでｄｆを追加すると行数がかわったりするのでdf7 = pd.DataFrame()ではなくてリスト　df_list = []　を使う。
####!!!!　df7 = pd.DataFrame()を使った例は次のブロックを参照。
# df5のdb_idを使ってすべてのLocaleを合わせたテーブルを作成する関数を呼ぶ。

df_list = []
i = 0
for db_num in df5.id:
    df8 = show_missing_values_across_locale(db_num, db_num, db_num, db_num, db_num, db_num, db_num, db_num, db_num, db_num)
    df_list.append(df8)
    i +=1

C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordat

C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordat

C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordat

C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordat

C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordat

...

C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordat

C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordat

C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordat

C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordat

C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(


In [360]:
df7 = pd.DataFrame(df_list)
df7

C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\core\internals\construction.py:576: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  values = np.array([convert(v) for v in values])


0
0                  skill               gb           ...
1                   skill                gb         ...
2                    skill                 gb       ...
3                         skill                     ...
4                       skill                    gb ...
...                                                 ...
1368            skill            gb            en   ...
1369                            skill               ...
1370                  skill                  gb     ...
1371                     skill                     g...
1372     skill     gb     en     de     es  fr_ca   ...

[1373 rows x 1 columns]

In [368]:
#Option ２　こっちの方がベターだけれども。df７になるまでに1373行あったはずが1243行になってしまう。
# df5のdb_idを使ってすべてのLocaleを合わせたテーブルを作成する関数を呼ぶ。

df7 = pd.DataFrame()
for db_num in df5.id:
    df8 = show_missing_values_across_locale(db_num, db_num, db_num, db_num, db_num, db_num, db_num, db_num, db_num, db_num)
    df7 = df7.append(df8)

C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\3411158149.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\3411158149.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.


C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\3411158149.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\3411158149.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLA

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\3411158149.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\3411158149.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLA

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\3411158149.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\3411158149.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLA

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\3411158149.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\3411158149.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLA

...

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\3411158149.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\3411158149.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLA

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\3411158149.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\3411158149.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLA

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\3411158149.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\3411158149.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLA

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\3411158149.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\3411158149.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLA

C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\3411158149.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\KeikoGolden\AppData\Local\Temp\ipykernel_5920\3411158149.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df7 = df7.append(df8)
C:\Users\KeikoGolden\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLA

In [369]:
df7

skill                            gb  \
0                2D Illustration               2D Illustration   
0               A+ Certification              A+ Certification   
0              Abrasive Blasting             Abrasive Blasting   
0         Administering Medicine        Administering Medicine   
0           Adobe Creative Cloud          Adobe Creative Cloud   
..                           ...                           ...   
0                   Gas Cylinder                  Gas Cylinder   
0   Learning Content Development  Learning Content Development   
0             Patient Engagement            Patient Engagement   
0          Teller Cash Dispenser         Teller Cash Dispenser   
0                          Andon                         Andon   

                              en                                  de  \
0                2D Illustration                        2D-Abbildung   
0               A+ Certification                   A+ Zertifizierung   
0              Abrasive Blasting                  Abrasives Strahlen   
0         Administering Medicine      Verabreichung von Medikamenten   
0           Adobe Creative Cloud                Adobe Creative Cloud   
..                           ...                                 ...   
0                   Gas Cylinder                Zylinderpräparierung   
0   Learning Content Development        Entwicklung von Lerninhalten   
0             Patient Engagement  Techniken für den Patientenkontakt   
0          Teller Cash Dispenser                       TCR-Ausgleich   
0                          Andon                               Andon   

                                        es  \
0                           2d ilustración   
0                         Certificación A+   
0                      Granallado abrasivo   
0           Administración de medicamentos   
0                     Adobe Creative Cloud   
..                                     ...   
0                          Cilindro de Gas   
0   desarrollo de Contenido de Aprendizaje   
0                  Compromiso del Paciente   
0        dispensador de Efectivo de Cajero   
0                                    Andon   

                                       fr_ca  \
0                            Illustration 2D   
0                           Certification A+   
0                         Nettoyage abrasive   
0                Administrer des médicaments   
0                       Adobe Creative Cloud   
..                                       ...   
0                           Bouteille de Gaz   
0   Développement de Contenu d'Apprentissage   
0                    Engagement des Patients   
0                   dispensateur de Caissier   
0                                      Andon   

                                          fr  \
0                            Illustration 2D   
0                           Certification A+   
0                           Décapage abrasif   
0                Administrer des médicaments   
0                       Adobe Creative Cloud   
..                                       ...   
0                           Bouteille de Gaz   
0   Développement de Contenu d'Apprentissage   
0                    Engagement des Patients   
0                   dispensateur de Caissier   
0                                      Andon   

                                            it                    jp  \
0                             Illustrazione 2D                2Dイラスト   
0                            Certificazione A+                A+認定資格   
0              Sabbiatrice (Abrasive Blasting)                 吹付け加工   
0                       Somministrare medicine                  薬剤投与   
0                         Adobe Creative Cloud  Adobe Creative Cloud   
..                                         ...                   ...   
0                             Cilindro del Gas                 ガスボンベ   
0   Apprendimento dello Sviluppo dei Contenuti            学習コンテンツの開発   
0             

In [352]:
df7 = df7.reset_index(drop=True)
df7

0
0                  skill               gb           ...
1                   skill                gb         ...
2                    skill                 gb       ...
3                         skill                     ...
4                       skill                    gb ...
...                                                 ...
1368            skill            gb            en   ...
1369                            skill               ...
1370                  skill                  gb     ...
1371                     skill                     g...
1372     skill     gb     en     de     es  fr_ca   ...

[1373 rows x 1 columns]

In [371]:
df7['serial_id'] = df2['serial_id']
df7

skill                            gb  \
0                2D Illustration               2D Illustration   
0               A+ Certification              A+ Certification   
0              Abrasive Blasting             Abrasive Blasting   
0         Administering Medicine        Administering Medicine   
0           Adobe Creative Cloud          Adobe Creative Cloud   
..                           ...                           ...   
0                   Gas Cylinder                  Gas Cylinder   
0   Learning Content Development  Learning Content Development   
0             Patient Engagement            Patient Engagement   
0          Teller Cash Dispenser         Teller Cash Dispenser   
0                          Andon                         Andon   

                              en                                  de  \
0                2D Illustration                        2D-Abbildung   
0               A+ Certification                   A+ Zertifizierung   
0              Abrasive Blasting                  Abrasives Strahlen   
0         Administering Medicine      Verabreichung von Medikamenten   
0           Adobe Creative Cloud                Adobe Creative Cloud   
..                           ...                                 ...   
0                   Gas Cylinder                Zylinderpräparierung   
0   Learning Content Development        Entwicklung von Lerninhalten   
0             Patient Engagement  Techniken für den Patientenkontakt   
0          Teller Cash Dispenser                       TCR-Ausgleich   
0                          Andon                               Andon   

                                        es  \
0                           2d ilustración   
0                         Certificación A+   
0                      Granallado abrasivo   
0           Administración de medicamentos   
0                     Adobe Creative Cloud   
..                                     ...   
0                          Cilindro de Gas   
0   desarrollo de Contenido de Aprendizaje   
0                  Compromiso del Paciente   
0        dispensador de Efectivo de Cajero   
0                                    Andon   

                                       fr_ca  \
0                            Illustration 2D   
0                           Certification A+   
0                         Nettoyage abrasive   
0                Administrer des médicaments   
0                       Adobe Creative Cloud   
..                                       ...   
0                           Bouteille de Gaz   
0   Développement de Contenu d'Apprentissage   
0                    Engagement des Patients   
0                   dispensateur de Caissier   
0                                      Andon   

                                          fr  \
0                            Illustration 2D   
0                           Certification A+   
0                           Décapage abrasif   
0                Administrer des médicaments   
0                       Adobe Creative Cloud   
..                                       ...   
0                           Bouteille de Gaz   
0   Développement de Contenu d'Apprentissage   
0                    Engagement des Patients   
0                   dispensateur de Caissier   
0                                      Andon   

                                            it                    jp  \
0                             Illustrazione 2D                2Dイラスト   
0                            Certificazione A+                A+認定資格   
0              Sabbiatrice (Abrasive Blasting)                 吹付け加工   
0                       Somministrare medicine                  薬剤投与   
0                         Adobe Creative Cloud  Adobe Creative Cloud   
..                                         ...                   ...   
0                             Cilindro del Gas                 ガスボンベ   
0   Apprendimento dello Sviluppo dei Contenuti            学習コンテンツの開発   
0             

In [353]:
#インデックス番号がdf３とdf７とでマッチしないので、マージは使えない。
df9 = pd.merge(df2[['serial_id']], df7, left_index = True, right_index = True )
df9

serial_id  \
0     5be4ac1d383aea1b473330d6   
1     5e55ad67870a2f223282b715   
2     5ec5ddfebd86b3287e0fc75d   
3     5a99c60dfc0da84a0c16c792   
4     5c2c3d12bb4cfc70c300b0e3   
...                        ...   
1368  5a9cf9d3fc0da84a0c1d9137   
1369  5ef9e908c1a2cb03a7f33ba7   
1370  5e41c4ebed09432018c02b0e   
1371  5eac70da3bb20c3124504a48   
1372  62b22a87d1037db062c05987   

                                                      0  
0                  skill               gb           ...  
1                   skill                gb         ...  
2                    skill                 gb       ...  
3                         skill                     ...  
4                       skill                    gb ...  
...                                                 ...  
1368            skill            gb            en   ...  
1369                            skill               ...  
1370                  skill                  gb     ...  
1371                     skill                     g...  
1372     skill     gb     en     de     es  fr_ca   ...  

[1373 rows x 2 columns]

In [355]:
df9.to_excel('sql_mapping_corresponding_to_each_row.xlsx')